# Лабораторная работа №n

Набор данных: ссылка

## Задание



## Контрольные вопросы



## Теория

Облако точек - это самый простой способ представления различных объектов в виде неупорядоченного набора точек в трехмерной плоскости. Такие данные можно получить с помощью сканирования предметов или их структуры с помощью 3D-датчиков, например LiDAR. Качественные облака точек с высокой точностью измерения позволяют представить цифровую версию реального мира.

<figure>
<center>
<img src='https://www.codeproject.com/KB/openGL/839389/bunny_points.PNG' />
<figcaption>Стэндфордский кролик</figcaption></center>
</figure>

Как правило, при глубоком обучении трехмерного облака точек необходимо решить две задачи: классификацию и сегментацию.
Основная проблема работы с облаком точек заключается в том, что типичная сверточная архитектура требует упорядоченный формат входных данных (например, изображение). Поскольку облако точек не является таким, общепринятые подходы заключаются в преобразовании данных в обычную 3D-воксельную сетку или проекцию.

В данной лабораторной работе используется эффективный подход для сегментации - DBSCAN.

DBSCAN (кластеризация на основе плотности) - плотностной алгоритм пространственной кластеризации с присутствием шума. Он определяет кластер произвольной формы в пространстве как максимальный набор точек, связанных достаточно высокой плотностью. Каждый объект, не содержащийся ни в одном кластере, автоматически считается шумом. Этот метод чувствителен к таким параметрам, как эпсилон (eps) и количество образцов в окрестностях для точки, которую следует рассматривать как основную точку (min_pts).

<figure>
<center>
<img src='https://www.researchgate.net/publication/342871651/figure/fig3/AS:912165510840320@1594488613526/The-graphical-representation-of-the-key-components-of-the-DBSCAN-algorithm-a-a.png' />
<figcaption>Работа алгоритма DBSCAN: (a) кластер, (b) основная точка (синяя точка), (c) пограничная точка (желтая точка), (d) точки, доступные для области</figcaption></center>
</figure>

DBSCAN выполняет итерацию по случайным точкам в наборе данных. Для каждой рассматриваемой точки он вычисляет окрестности этой точки, и если эта окрестность содержит более определенного количества точек, она включается в область. Каждая соседняя точка проходит через один и тот же процесс до тех пор, пока она больше не сможет расширять кластер. Если рассматриваемая точка не является внутренней точкой, т.е. у нее недостаточно соседей, она будет помечена как шум. Это позволяет DBSCAN быть устойчивым к выбросам.

## Импорт библиотек

In [ ]:
!pip install open3d

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 422.5/422.5 MB 3.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.3/75.3 KB 9.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.9/9.9 MB 96.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 75.2 MB/s eta 0:00:00
  Attempting uninstall: nbformat
    Found existing installation: nbformat 5.7.3
    Uninstalling nbformat-5.7.3:
      Successfully uninstalled nbformat-5.7.3


In [ ]:
import numpy as np
import open3d as o3d
from sklearn.cluster import DBSCAN, OPTICS
import matplotlib.pyplot as plt
import plotly.graph_objects as go

Метки (labels) варьируются от -1 до n, где -1 указывает, что это точка с "шумом", а значения от 0 до n - это метки кластера, присвоенные соответствующей точке. Для удобства каждой точке определенной метки присваивается свой цвет.

max_label сохраняет максимальное значение в списке меток. Для зашумленных точек со значением метки "-1" позже присваивается значение черного цвета (black).

In [ ]:
# функция для сегментации
def segment_pcd(X, pcd, points, user_eps, user_min_samp):
  clustering = DBSCAN(eps=user_eps, min_samples=user_min_samp, algorithm='ball_tree').fit(X)
  labels=clustering.labels_
  
  max_label = labels.max() + 1

  obj_points=[]
  for i in range(max_label):
    idx_labels = np.where(labels==i)
    obj_points.append(points[idx_labels])

  idx_layer=np.where(labels<0)
  colors = plt.get_cmap("tab20")(labels / (max_label if max_label > 0 else 1))
  colors[labels < 0] = 0
  pcd.colors = o3d.utility.Vector3dVector(colors[:, :3])

  return pcd, colors, max_label, obj_points

In [ ]:
# функция для графического отображения облака точек
def draw_plot(points, colors=None):
  fig = go.Figure(
      data=[
          go.Scatter3d(
              x=points[:,0], y=points[:,1], z=points[:,2], 
              mode='markers',
              marker=dict(size=1, color=colors)
          )
      ],
      layout=dict(
          scene=dict(
              xaxis=dict(visible=False),
              yaxis=dict(visible=False),
              zaxis=dict(visible=False)
          )
      )
      )
  return fig

In [ ]:
# функция присваивания цвета точке
def add_color(pcd, colors):
  if pcd.has_colors():
    colors = np.asarray(pcd.colors)
  elif pcd.has_normals():
    colors = (0.0, 0.5, 0.5) + np.asarray(pcd.normals) * 0.5
  else:
    pcd.paint_uniform_color((0.0, 0.0, 0.0))
    colors = np.asarray(pcd.colors)
  return pcd, colors

In [ ]:
# функция для сегментации
def np_to_pcd(points):
  colors = np.zeros(points.shape)
  for i in range(0,points.shape[0]):
    colors[i][0] = 0.12156863
    colors[i][1] = 0.46666667
    colors[i][2] = 0.70588235
  point_cloud = o3d.geometry.PointCloud()
  point_cloud.points = o3d.utility.Vector3dVector(points)
  point_cloud.colors = o3d.utility.Vector3dVector(colors)
  return point_cloud

## Загрузка набора данных

In [ ]:
pcd = o3d.io.read_point_cloud("/content/example.pcd")
points = np.asarray(pcd.points)
colors = None

In [ ]:
draw_plot(points, colors)

Если помимо деревьев в обаке точек присутсвует земля, то для лучшего результата сегментации ее нужно убрать. Код, представленный ниже, удаляет ее с помощью вычисления нормали (функция estimate_normals) на основе метода k-ближайших соседей.

In [ ]:
#удаление земли из облака точек
idx_all = np.empty((points.shape[0],1), dtype = int)
for i in range(points.shape[0]):
  idx_all[i][0] = i
pointsres = points

pcd.estimate_normals(search_param=o3d.geometry.KDTreeSearchParamHybrid(radius=0.1, max_nn=30))
normals = np.asarray(pcd.normals)

idx_normals=np.where((abs(normals[:,2])<0.05))
idx_ground=np.where(points[:,2]>np.min(points[:,2]+5))
idx_wronglyfiltered=np.setdiff1d(idx_ground, idx_normals)
idx_retained=np.append(idx_normals, idx_wronglyfiltered)
points = points[idx_retained]
idx_retained = np.asarray(idx_retained)
idx_retained = np.transpose(idx_retained)
          
idx_inv=np.setdiff1d(idx_all, idx_retained)
points_ground = pointsres[idx_inv]
point_cloud_ground = np_to_pcd(points_ground)
          
point_cloud = np_to_pcd(points)

colors_ground = np.zeros(points_ground.shape)
for i in range(0,points_ground.shape[0]):
  colors_ground[i][0] = 1
  colors_ground[i][1] = 0.2
  colors_ground[i][2] = 0.2

point_cloud_ground.colors = o3d.utility.Vector3dVector(colors_ground)
pcd = point_cloud

In [ ]:
pcd, colors = add_color(pcd, colors)
X = np.asarray(pcd.points)

In [ ]:
# настройка основных параметров модели
# eps - размер окрестности точки
# min_pts - минимальное кол-во точек в окрестности

eps = 0.78
min_pts = 135

In [ ]:
max_label, obj_points = None, None
new_pcd, colors, max_label, obj_points = segment_pcd(X, pcd, points, eps, min_pts)
print(f"Распознано {max_label} объектов в облаке точек")

Распознано 5 объектов в облаке точек


In [ ]:
points = np.asarray(pcd.points)
new_pcd, colors = add_color(new_pcd, colors)

draw_plot(points, colors)